# Project 3: Smart Beta Portfolio and Portfolio Optimization

## Overview


Smart beta has a broad meaning, but we can say in practice that when we use the universe of stocks from an index, and then apply some weighting scheme other than market cap weighting, it can be considered a type of smart beta fund.  A Smart Beta portfolio generally gives investors exposure or "beta" to one or more types of market characteristics (or factors) that are believed to predict prices while giving investors a diversified broad exposure to a particular market. Smart Beta portfolios generally target momentum, earnings quality, low volatility, and dividends or some combination. Smart Beta Portfolios are generally rebalanced infrequently and follow relatively simple rules or algorithms that are passively managed.  Model changes to these types of funds are also rare requiring prospectus filings with US Security and Exchange Commission in the case of US focused mutual funds or ETFs.. Smart Beta portfolios are generally long-only, they do not short stocks.

In contrast, a purely alpha-focused quantitative fund may use multiple models or algorithms to create a portfolio. The portfolio manager retains discretion in upgrading or changing the types of models and how often to rebalance the portfolio in attempt to maximize performance in comparison to a stock benchmark.  Managers may have discretion to short stocks in portfolios.

Imagine you're a portfolio manager, and wish to try out some different portfolio weighting methods.

One way to design portfolio is to look at certain accounting measures (fundamentals) that, based on past trends, indicate stocks that produce better results.  


For instance, you may start with a hypothesis that dividend-issuing stocks tend to perform better than stocks that do not. This may not always be true of all companies; for instance, Apple does not issue dividends, but has had good historical performance.  The hypothesis about dividend-paying stocks may go something like this: 

Companies that regularly issue dividends may also be more prudent in allocating their available cash, and may indicate that they are more conscious of prioritizing shareholder interests.  For example, a CEO may decide to reinvest cash into pet projects that produce low returns.  Or, the CEO may do some analysis, identify that reinvesting within the company produces lower returns compared to a diversified portfolio, and so decide that shareholders would be better served if they were given the cash (in the form of dividends).  So according to this hypothesis, dividends may be both a proxy for how the company is doing (in terms of earnings and cash flow), but also a signal that the company acts in the best interest of its shareholders.  Of course, it's important to test whether this works in practice.


You may also have another hypothesis, with which you wish to design a portfolio that can then be made into an ETF.  You may find that investors may wish to invest in passive beta funds, but wish to have less risk exposure (less volatility) in their investments.  The goal of having a low volatility fund that still produces returns similar to an index may be appealing to investors who have a shorter investment time horizon, and so are more risk averse.

So the objective of your proposed portfolio is to design a portfolio that closely tracks an index, while also minimizing the portfolio variance.  Also, if this portfolio can match the returns of the index with less volatility, then it has a higher risk-adjusted return (same return, lower volatility).

Smart Beta ETFs can be designed with both of these two general methods (among others): alternative weighting and minimum volatility ETF.


## Instructions
Each problem consists of a function to implement and instructions on how to implement the function.  The parts of the function that need to be implemented are marked with a `# TODO` comment. After implementing the function, run the cell to test it against the unit tests we've provided. For each problem, we provide one or more unit tests from our `project_tests` package. These unit tests won't tell you if your answer is correct, but will warn you of any major errors. Your code will be checked for the correct solution when you submit it to Udacity.

## Packages
When you implement the functions, you'll only need to you use the packages you've used in the classroom, like [Pandas](https://pandas.pydata.org/) and [Numpy](http://www.numpy.org/). These packages will be imported for you. We recommend you don't add any import statements, otherwise the grader might not be able to run your code.

The other packages that we're importing are `helper`, `project_helper`, and `project_tests`. These are custom packages built to help you solve the problems.  The `helper` and `project_helper` module contains utility functions and graph functions. The `project_tests` contains the unit tests for all the problems.
### Install Packages

In [1]:
import sys
!{sys.executable} -m pip install -r requirements.txt

    100% |████████████████████████████████| 13.9MB 33kB/s  eta 0:00:01
  Found existing installation: numpy 1.14.5
    Uninstalling numpy-1.14.5:
      Successfully uninstalled numpy-1.14.5
You are using pip version 9.0.1, however version 18.1 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


### Load Packages

In [2]:
import pandas as pd
import numpy as np
import helper
import project_helper
import project_tests

/opt/conda/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


## Market Data
### Load Data
For this universe of stocks, we'll be selecting large dollar volume stocks. We're using this universe, since it is highly liquid.

In [3]:
df = pd.read_csv('../../data/project_3/eod-quotemedia.csv')

percent_top_dollar = 0.2
high_volume_symbols = project_helper.large_dollar_volume_stocks(df, 'adj_close', 'adj_volume', percent_top_dollar)
df = df[df['ticker'].isin(high_volume_symbols)]

close = df.reset_index().pivot(index='date', columns='ticker', values='adj_close')
volume = df.reset_index().pivot(index='date', columns='ticker', values='adj_volume')
dividends = df.reset_index().pivot(index='date', columns='ticker', values='dividends')

### View Data
To see what one of these 2-d matrices looks like, let's take a look at the closing prices matrix.

In [4]:
project_helper.print_dataframe(close)

# Part 1: Smart Beta Portfolio
In Part 1 of this project, you'll build a portfolio using dividend yield to choose the portfolio weights. A portfolio such as this could be incorporated into a smart beta ETF.  You'll compare this portfolio to a market cap weighted index to see how well it performs. 

Note that in practice, you'll probably get the index weights from a data vendor (such as companies that create indices, like MSCI, FTSE, Standard and Poor's), but for this exercise we will simulate a market cap weighted index.

## Index Weights
The index we'll be using is based on large dollar volume stocks. Implement `generate_dollar_volume_weights` to generate the weights for this index. For each date, generate the weights based on dollar volume traded for that date. For example, assume the following is close prices and volume data:
```
                 Prices
               A         B         ...
2013-07-08     2         2         ...
2013-07-09     5         6         ...
2013-07-10     1         2         ...
2013-07-11     6         5         ...
...            ...       ...       ...

                 Volume
               A         B         ...
2013-07-08     100       340       ...
2013-07-09     240       220       ...
2013-07-10     120       500       ...
2013-07-11     10        100       ...
...            ...       ...       ...
```
The weights created from the function `generate_dollar_volume_weights` should be the following:
```
               A         B         ...
2013-07-08     0.126..   0.194..   ...
2013-07-09     0.759..   0.377..   ...
2013-07-10     0.075..   0.285..   ...
2013-07-11     0.037..   0.142..   ...
...            ...       ...       ...
```

In [5]:
def generate_dollar_volume_weights(close, volume):
    """
    Generate dollar volume weights.

    Parameters
    ----------
    close : DataFrame
        Close price for each ticker and date
    volume : str
        Volume for each ticker and date

    Returns
    -------
    dollar_volume_weights : DataFrame
        The dollar volume weights for each ticker and date
    """
    assert close.index.equals(volume.index)
    assert close.columns.equals(volume.columns)
    
    print(close)
    print(volume)
    
    dollar_volume = close*volume
    print(dollar_volume)
    # found the request a bit misleading, initially computed with cap_per_stock..
    cap_per_date = dollar_volume.sum(axis=1)
    print(cap_per_date)

    return dollar_volume.div(cap_per_date, axis='index')

project_tests.test_generate_dollar_volume_weights(generate_dollar_volume_weights)

                  CAAO        VCFM        GGCI
2013-10-10 35.44110000 34.17990000 34.02230000
2013-10-11 92.11310000 91.05430000 90.95720000
2013-10-12 57.97080000 57.78140000 58.19820000
2013-10-13 34.17050000 92.45300000 58.51070000
                        CAAO              VCFM              GGCI
2013-10-10  9836830.00000000 17807200.00000000  8829820.00000000
2013-10-11 82242700.00000000 68531500.00000000 48160100.00000000
2013-10-12 16234800.00000000 13052700.00000000  9512010.00000000
2013-10-13 10674200.00000000 56831300.00000000  9316010.00000000
                          CAAO                VCFM                GGCI
2013-10-10  348628075.71300000  608648315.28000009  300410784.98600000
2013-10-11 7575630049.36999989 6240087760.44999981 4380507847.72000027
2013-10-12  941144343.83999991  754203279.77999997  553581860.38199997
2013-10-13  364742751.09999996 5254224178.90000057  545086266.30700004
2013-10-10    1257687175.97900009
2013-10-11   18196225657.54000092
2013-10-12    224

### View Data
Let's generate the index weights using `generate_dollar_volume_weights` and view them using a heatmap.

In [6]:
index_weights = generate_dollar_volume_weights(close, volume)
project_helper.plot_weights(index_weights, 'Index Weights')

ticker             AAL         AAPL        ABBV         ABT          AGN  \
date                                                                       
2013-07-01 16.17609308  53.10917319 34.92447839 31.42538772 122.62751990   
2013-07-02 15.81983388  54.31224742 35.42807578 31.27288084 121.05361758   
2013-07-03 16.12794994  54.61204262 35.44486235 30.72565028 121.21003024   
2013-07-05 16.21460758  54.17338125 35.85613355 31.32670680 123.53666845   
2013-07-08 16.31089385  53.86579916 36.66188936 31.76628544 123.65397794   
2013-07-09 16.71529618  54.81320389 36.35973093 31.16522893 122.89146626   
2013-07-10 16.53235227  54.60295791 36.85493502 31.16522893 121.28823656   
2013-07-11 16.72492481  55.45406479 37.08155384 31.85599537 122.19738511   
2013-07-12 16.90786872  55.35309481 38.15724076 31.81096287 123.35092842   
2013-07-15 17.10044125  55.47379158 37.79303181 31.95506689 122.37334934   
2013-07-16 17.28338516  55.83133953 37.10696377 32.15320992 120.08581429   
2013-07-17 1

## Portfolio Weights
Now that we have the index weights, let's choose the portfolio weights based on dividend. You would normally calculate the weights based on trailing dividend yield, but we'll simplify this by just calculating the total dividend yield over time.

Implement `calculate_dividend_weights` to return the weights for each stock based on its total dividend yield over time. This is similar to generating the weight for the index, but it's using dividend data instead.
For example, assume the following is `dividends` data:
```
                 Prices
               A         B
2013-07-08     0         0
2013-07-09     0         1
2013-07-10     0.5       0
2013-07-11     0         0
2013-07-12     2         0
...            ...       ...
```
The weights created from the function `calculate_dividend_weights` should be the following:
```
               A         B
2013-07-08     NaN       NaN
2013-07-09     0         1
2013-07-10     0.333..   0.666..
2013-07-11     0.333..   0.666..
2013-07-12     0.714..   0.285..
...            ...       ...
```

In [7]:
def calculate_dividend_weights(dividends):
    """
    Calculate dividend weights.

    Parameters
    ----------
    dividends : DataFrame
        Dividend for each stock and date

    Returns
    -------
    dividend_weights : DataFrame
        Weights for each stock and date
    """
    
    # test data from above
    #dividends = pd.DataFrame(data=[(0, 0), (0, 1), (0.5, 0), (0, 0), (2, 0)], index=['2013-07-08','2013-07-09','2013-07-10','2013-07-11','2013-07-12'], 
    #             columns=['A','B'])
    
    print("Dividends")
    print(dividends)
    
    cumulAcrossRows = dividends.cumsum(axis=0)
    print("cumulAcrossRows")
    print(cumulAcrossRows)
    
    cumulAcrossCols = cumulAcrossRows.sum(axis=1)
    print("cumulAcrossCols")
    print(cumulAcrossCols)
    
    dividend_weights = cumulAcrossRows.div(cumulAcrossCols, axis='index')
    return dividend_weights

project_tests.test_calculate_dividend_weights(calculate_dividend_weights)

Dividends
                 CAJJ        RQY        YTL
2003-03-06 0.00000000 0.00000000 0.00000000
2003-03-07 0.00000000 0.00000000 0.10000000
2003-03-08 0.00000000 1.00000000 0.30000000
2003-03-09 0.00000000 0.20000000 0.00000000
cumulAcrossRows
                 CAJJ        RQY        YTL
2003-03-06 0.00000000 0.00000000 0.00000000
2003-03-07 0.00000000 0.00000000 0.10000000
2003-03-08 0.00000000 1.00000000 0.40000000
2003-03-09 0.00000000 1.20000000 0.40000000
cumulAcrossCols
2003-03-06   0.00000000
2003-03-07   0.10000000
2003-03-08   1.40000000
2003-03-09   1.60000000
dtype: float64
Tests Passed


### View Data
Just like the index weights, let's generate the ETF weights and view them using a heatmap.

In [8]:
etf_weights = calculate_dividend_weights(dividends)
project_helper.plot_weights(etf_weights, 'ETF Weights')

Dividends
ticker            AAL       AAPL       ABBV        ABT        AGN        AIG  \
date                                                                           
2013-07-01 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-02 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-03 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-05 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-08 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-09 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-10 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-11 0.00000000 0.00000000 0.40000000 0.14000000 0.00000000 0.00000000   
2013-07-12 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-15 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000 0.00000000   
2013-07-16 0.00000000 0.000000

## Returns
Implement `generate_returns` to generate returns data for all the stocks and dates from price data. You might notice we're implementing returns and not log returns. Since we're not dealing with volatility, we don't have to use log returns.

In [9]:
def generate_returns(prices):
    """
    Generate returns for ticker and date.

    Parameters
    ----------
    prices : DataFrame
        Price for each ticker and date

    Returns
    -------
    returns : Dataframe
        The returns for each ticker and date
    """

    return (prices/prices.shift(1)) - 1

project_tests.test_generate_returns(generate_returns)

Tests Passed


### View Data
Let's generate the closing returns using `generate_returns` and view them using a heatmap.

In [10]:
returns = generate_returns(close)
project_helper.plot_returns(returns, 'Close Returns')

## Weighted Returns
With the returns of each stock computed, we can use it to compute the returns for an index or ETF. Implement `generate_weighted_returns` to create weighted returns using the returns and weights.

In [11]:
def generate_weighted_returns(returns, weights):
    """
    Generate weighted returns.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date
    weights : DataFrame
        Weights for each ticker and date

    Returns
    -------
    weighted_returns : DataFrame
        Weighted returns for each ticker and date
    """
    assert returns.index.equals(weights.index)
    assert returns.columns.equals(weights.columns)

    return returns*weights

project_tests.test_generate_weighted_returns(generate_weighted_returns)

Tests Passed


### View Data
Let's generate the ETF and index returns using `generate_weighted_returns` and view them using a heatmap.

In [12]:
index_weighted_returns = generate_weighted_returns(returns, index_weights)
etf_weighted_returns = generate_weighted_returns(returns, etf_weights)
project_helper.plot_returns(index_weighted_returns, 'Index Returns')
project_helper.plot_returns(etf_weighted_returns, 'ETF Returns')

## Cumulative Returns
To compare performance between the ETF and Index, we're going to calculate the tracking error. Before we do that, we first need to calculate the index and ETF comulative returns. Implement `calculate_cumulative_returns` to calculate the cumulative returns over time given the returns.

In [13]:
def calculate_cumulative_returns(returns):
    """
    Calculate cumulative returns.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date

    Returns
    -------
    cumulative_returns : Pandas Series
        Cumulative returns for each date
    """
    
    print("Returns")
    print(returns)
    #returns = returns.dropna()
    
    print(len(returns))
    
    cumulative_returns = returns.cumsum(axis=0)
    print("Cumulative Returns")
    print(cumulative_returns)
    
    # 1 + r_i, where r_i is the portfolio return at a certain date i
    sumReturns = returns.sum(axis=1) + 1
    print("Sum")
    print(sumReturns)
    
    # multiply them together (1+r1)(1+r2)..
    cumulative_returns = sumReturns.cumprod(axis=0)
    print("Result")
    print(cumulative_returns)
    
    # why is there no -1 at the end?
    # according to the lesson and Wikipedia, the formula is
    # (1+r1)(1+r2)...(1+rN) - 1 ... but we do not do -1 here
    return cumulative_returns

project_tests.test_calculate_cumulative_returns(calculate_cumulative_returns)

Returns
                   AAN        DCGS         DJR
2012-07-28         nan         nan         nan
2012-07-29  1.59904743  1.66397210  1.67345829
2012-07-30 -0.37065629 -0.36541822 -0.36015840
2012-07-31 -0.41055669  0.60004777  0.00536958
4
Cumulative Returns
                  AAN       DCGS        DJR
2012-07-28        nan        nan        nan
2012-07-29 1.59904743 1.66397210 1.67345829
2012-07-30 1.22839114 1.29855388 1.31329989
2012-07-31 0.81783445 1.89860165 1.31866947
Sum
2012-07-28           nan
2012-07-29    5.93647782
2012-07-30   -0.09623291
2012-07-31    1.19486066
dtype: float64
Result
2012-07-28           nan
2012-07-29    5.93647782
2012-07-30   -0.57128454
2012-07-31   -0.68260542
dtype: float64
Tests Passed


### View Data
Let's generate the ETF and index cumulative returns using `calculate_cumulative_returns` and compare the two.

In [14]:
index_weighted_cumulative_returns = calculate_cumulative_returns(index_weighted_returns)
etf_weighted_cumulative_returns = calculate_cumulative_returns(etf_weighted_returns)
project_helper.plot_benchmark_returns(index_weighted_cumulative_returns, etf_weighted_cumulative_returns, 'Smart Beta ETF vs Index')

Returns
ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 -0.00008007  0.00308984  0.00004768 -0.00001880 -0.00003423   
2013-07-03  0.00009093  0.00074662  0.00000167 -0.00018529  0.00000450   
2013-07-05  0.00001716 -0.00091335  0.00003497  0.00008758  0.00005552   
2013-07-08  0.00001590 -0.00052257  0.00007514  0.00007710  0.00000238   
2013-07-09  0.00009451  0.00177325 -0.00002380 -0.00012663 -0.00001420   
2013-07-10 -0.00004895 -0.00034661  0.00003637  0.00000000 -0.00004299   
2013-07-11  0.00003254  0.00139306  0.00001830  0.00012582  0.00002055   
2013-07-12  0.00003548 -0.00012769  0.00011425 -0.00000507  0.00002572   
2013-07-15  0.00003910  0.00016769 -0.00002700  0.00002153 -0.00002676   
2013-07-16  0.00004287  0.00043884 -0.00005637  0.00003814 -0.00005587   
2013-07-17  0.00018322  0.0000

## Tracking Error
In order to check the performance of the smart beta portfolio, we can calculate the annualized tracking error against the index. Implement `tracking_error` to return the tracking error between the ETF and benchmark.

For reference, we'll be using the following annualized tracking error function:
$$ TE = \sqrt{252} * SampleStdev(r_p - r_b) $$

Where $ r_p $ is the portfolio/ETF returns and $ r_b $ is the benchmark returns.

_Note: When calculating the sample standard deviation, the delta degrees of freedom is 1, which is the also the default value._

In [15]:
def tracking_error(benchmark_returns_by_date, etf_returns_by_date):
    """
    Calculate the tracking error.

    Parameters
    ----------
    benchmark_returns_by_date : Pandas Series
        The benchmark returns for each date
    etf_returns_by_date : Pandas Series
        The ETF returns for each date

    Returns
    -------
    tracking_error : float
        The tracking error
    """
    assert benchmark_returns_by_date.index.equals(etf_returns_by_date.index)
    
    diff = etf_returns_by_date - benchmark_returns_by_date
    #ddof=1 to normalize by N-1 and get the sample standard dev
    #as opposed to the population standard dev (with ddof=0)
    stdev = diff.std(ddof=1)
    tracking_error = np.sqrt(252)*stdev

    return tracking_error

project_tests.test_tracking_error(tracking_error)

Tests Passed


### View Data
Let's generate the tracking error using `tracking_error`.

In [16]:
smart_beta_tracking_error = tracking_error(np.sum(index_weighted_returns, 1), np.sum(etf_weighted_returns, 1))
print('Smart Beta Tracking Error: {}'.format(smart_beta_tracking_error))

Smart Beta Tracking Error: 0.10207614832007529


# Part 2: Portfolio Optimization

Now, let's create a second portfolio.  We'll still reuse the market cap weighted index, but this will be independent of the dividend-weighted portfolio that we created in part 1.

We want to both minimize the portfolio variance and also want to closely track a market cap weighted index.  In other words, we're trying to minimize the distance between the weights of our portfolio and the weights of the index.

$Minimize \left [ \sigma^2_p + \lambda \sqrt{\sum_{1}^{m}(weight_i - indexWeight_i)^2} \right  ]$ where $m$ is the number of stocks in the portfolio, and $\lambda$ is a scaling factor that you can choose.

Why are we doing this? One way that investors evaluate a fund is by how well it tracks its index. The fund is still expected to deviate from the index within a certain range in order to improve fund performance.  A way for a fund to track the performance of its benchmark is by keeping its asset weights similar to the weights of the index.  We’d expect that if the fund has the same stocks as the benchmark, and also the same weights for each stock as the benchmark, the fund would yield about the same returns as the benchmark. By minimizing a linear combination of both the portfolio risk and distance between portfolio and benchmark weights, we attempt to balance the desire to minimize portfolio variance with the goal of tracking the index.


## Covariance
Implement `get_covariance_returns` to calculate the covariance of the `returns`. We'll use this to calculate the portfolio variance.

If we have $m$ stock series, the covariance matrix is an $m \times m$ matrix containing the covariance between each pair of stocks.  We can use [`Numpy.cov`](https://docs.scipy.org/doc/numpy/reference/generated/numpy.cov.html) to get the covariance.  We give it a 2D array in which each row is a stock series, and each column is an observation at the same period of time. For any `NaN` values, you can replace them with zeros using the [`DataFrame.fillna`](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.fillna.html) function.

The covariance matrix $\mathbf{P} = 
\begin{bmatrix}
\sigma^2_{1,1} & ... & \sigma^2_{1,m} \\ 
... & ... & ...\\
\sigma_{m,1} & ... & \sigma^2_{m,m}  \\
\end{bmatrix}$

In [17]:
def get_covariance_returns(returns):
    """
    Calculate covariance matrices.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date

    Returns
    -------
    returns_covariance  : 2 dimensional Ndarray
        The covariance of the returns
    """
    
    print("Returns")
    print(returns)
    
    returns = returns.fillna(0)
    print(returns)
    
    P = np.cov(returns, rowvar=False)
    
    print(P)
    
    return P

project_tests.test_get_covariance_returns(get_covariance_returns)

Returns
                   RYY        HPYP        THDD
2000-06-11         nan         nan         nan
2000-06-12  1.59904743  1.66397210  1.67345829
2000-06-13 -0.37065629 -0.36541822 -0.36015840
2000-06-14 -0.41055669  0.60004777  0.00536958
                   RYY        HPYP        THDD
2000-06-11  0.00000000  0.00000000  0.00000000
2000-06-12  1.59904743  1.66397210  1.67345829
2000-06-13 -0.37065629 -0.36541822 -0.36015840
2000-06-14 -0.41055669  0.60004777  0.00536958
[[0.89856076 0.7205586  0.8458721 ]
 [0.7205586  0.78707297 0.76450378]
 [0.8458721  0.76450378 0.83182775]]
Tests Passed


### View Data
Let's look at the covariance generated from `get_covariance_returns`.

In [18]:
covariance_returns = get_covariance_returns(returns)
covariance_returns = pd.DataFrame(covariance_returns, returns.columns, returns.columns)

covariance_returns_correlation = np.linalg.inv(np.diag(np.sqrt(np.diag(covariance_returns))))
covariance_returns_correlation = pd.DataFrame(
    covariance_returns_correlation.dot(covariance_returns).dot(covariance_returns_correlation),
    covariance_returns.index,
    covariance_returns.columns)

project_helper.plot_covariance_returns_correlation(
    covariance_returns_correlation,
    'Covariance Returns Correlation Matrix')

Returns
ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 -0.02202381  0.02265285  0.01441961 -0.00485298 -0.01283482   
2013-07-03  0.01947657  0.00551985  0.00047382 -0.01749857  0.00129209   
2013-07-05  0.00537313 -0.00803232  0.01160313  0.01956204  0.01919510   
2013-07-08  0.00593824 -0.00567773  0.02247191  0.01403207  0.00094959   
2013-07-09  0.02479339  0.01758824 -0.00824176 -0.01892121 -0.00616650   
2013-07-10 -0.01094470 -0.00383568  0.01361958  0.00000000 -0.01304590   
2013-07-11  0.01164822  0.01558719  0.00614894  0.02216465  0.00749577   
2013-07-12  0.01093840 -0.00182079  0.02900868 -0.00141363  0.00944000   
2013-07-15  0.01138952  0.00218049 -0.00954495  0.00453001 -0.00792519   
2013-07-16  0.01069820  0.00644535 -0.01815329  0.00620068 -0.01869308   
2013-07-17  0.02785515  0.0002

### portfolio variance
We can write the portfolio variance $\sigma^2_p = \mathbf{x^T} \mathbf{P} \mathbf{x}$

Recall that the $\mathbf{x^T} \mathbf{P} \mathbf{x}$ is called the quadratic form.
We can use the cvxpy function `quad_form(x,P)` to get the quadratic form.

### Distance from index weights
We want portfolio weights that track the index closely.  So we want to minimize the distance between them.
Recall from the Pythagorean theorem that you can get the distance between two points in an x,y plane by adding the square of the x and y distances and taking the square root.  Extending this to any number of dimensions is called the L2 norm.  So: $\sqrt{\sum_{1}^{n}(weight_i - indexWeight_i)^2}$  Can also be written as $\left \| \mathbf{x} - \mathbf{index} \right \|_2$.  There's a cvxpy function called [norm()](https://www.cvxpy.org/api_reference/cvxpy.atoms.other_atoms.html#norm)
`norm(x, p=2, axis=None)`.  The default is already set to find an L2 norm, so you would pass in one argument, which is the difference between your portfolio weights and the index weights.

### objective function
We want to minimize both the portfolio variance and the distance of the portfolio weights from the index weights.
We also want to choose a `scale` constant, which is $\lambda$ in the expression. 

$\mathbf{x^T} \mathbf{P} \mathbf{x} + \lambda \left \| \mathbf{x} - \mathbf{index} \right \|_2$


This lets us choose how much priority we give to minimizing the difference from the index, relative to minimizing the variance of the portfolio.  If you choose a higher value for `scale` ($\lambda$).

We can find the objective function using cvxpy `objective = cvx.Minimize()`.  Can you guess what to pass into this function?



### constraints
We can also define our constraints in a list.  For example, you'd want the weights to sum to one. So $\sum_{1}^{n}x = 1$.  You may also need to go long only, which means no shorting, so no negative weights.  So $x_i >0 $ for all $i$. you could save a variable as `[x >= 0, sum(x) == 1]`, where x was created using `cvx.Variable()`.

### optimization
So now that we have our objective function and constraints, we can solve for the values of $\mathbf{x}$.
cvxpy has the constructor `Problem(objective, constraints)`, which returns a `Problem` object.

The `Problem` object has a function solve(), which returns the minimum of the solution.  In this case, this is the minimum variance of the portfolio.

It also updates the vector $\mathbf{x}$.

We can check out the values of $x_A$ and $x_B$ that gave the minimum portfolio variance by using `x.value`

In [19]:
import cvxpy as cvx

def get_optimal_weights(covariance_returns, index_weights, scale=2.0):
    """
    Find the optimal weights.

    Parameters
    ----------
    covariance_returns : 2 dimensional Ndarray
        The covariance of the returns
    index_weights : Pandas Series
        Index weights for all tickers at a period in time
    scale : int
        The penalty factor for weights the deviate from the index 
    Returns
    -------
    x : 1 dimensional Ndarray
        The solution for x
    """
    assert len(covariance_returns.shape) == 2
    assert len(index_weights.shape) == 1
    assert covariance_returns.shape[0] == covariance_returns.shape[1]  == index_weights.shape[0]
    
    print ("Index weights")
    print(index_weights)
    print(len(index_weights))
    x = cvx.Variable(len(index_weights))
    
    variance = cvx.quad_form(x,covariance_returns)
    
    distance = cvx.norm(x - index_weights)
    
    objective = cvx.Minimize(variance + scale * distance)
    
    constraints = [sum(x) == 1, x >= 0]
    
    problem = cvx.Problem(objective, constraints)
    
    # optimal objectiva value
    opt = problem.solve()
    
    # return the optimal values of x
    print("Optimal Xs:")
    print(x.value)
    return x.value

project_tests.test_get_optimal_weights(get_optimal_weights)

Index weights
A   0.23623892
B   0.01256280
C   0.75119820
dtype: float64
3
Optimal Xs:
[0.23623897 0.01256285 0.75119817]
Tests Passed


## Optimized Portfolio
Using the `get_optimal_weights` function, let's generate the optimal ETF weights without rebalanceing. We can do this by feeding in the covariance of the entire history of data. We also need to feed in a set of index weights. We'll go with the average weights of the index over time.

In [20]:
raw_optimal_single_rebalance_etf_weights = get_optimal_weights(covariance_returns.values, index_weights.iloc[-1])
optimal_single_rebalance_etf_weights = pd.DataFrame(
    np.tile(raw_optimal_single_rebalance_etf_weights, (len(returns.index), 1)),
    returns.index,
    returns.columns)

Index weights
ticker
AAL     0.00505383
AAPL    0.04996914
ABBV    0.00507628
ABT     0.00344529
AGN     0.00631443
AIG     0.00723481
AMAT    0.00628914
AMGN    0.00690689
AMZN    0.05022972
APC     0.00367206
AVGO    0.00923578
AXP     0.00420389
BA      0.00659224
BAC     0.03065369
BIIB    0.00570220
BMY     0.00386121
C       0.01591180
CAT     0.00755899
CBS     0.00230404
CELG    0.00784448
CHTR    0.00719021
CMCSA   0.01067014
CMG     0.00471339
COP     0.00600604
COST    0.01150549
CRM     0.00522686
CSCO    0.01085341
CVS     0.00530558
CVX     0.00845056
DAL     0.00402521
           ...    
NVDA    0.04032500
ORCL    0.00993157
OXY     0.00412432
PEP     0.00568072
PFE     0.00669019
PG      0.00783857
PM      0.00553949
PXD     0.00366138
QCOM    0.00714256
REGN    0.00952813
SBUX    0.00709645
SLB     0.00780563
T       0.01234318
TGT     0.00308681
TWX     0.00712188
TXN     0.00539759
UAL     0.00398087
UNH     0.00669447
UNP     0.00567573
UPS     0.00357363
USB     0.

With our ETF weights built, let's compare it to the index. Run the next cell to calculate the ETF returns and compare it to the index returns.

In [21]:
optim_etf_returns = generate_weighted_returns(returns, optimal_single_rebalance_etf_weights)
optim_etf_cumulative_returns = calculate_cumulative_returns(optim_etf_returns)
project_helper.plot_benchmark_returns(index_weighted_cumulative_returns, optim_etf_cumulative_returns, 'Optimized ETF vs Index')

optim_etf_tracking_error = tracking_error(np.sum(index_weighted_returns, 1), np.sum(optim_etf_returns, 1))
print('Optimized ETF Tracking Error: {}'.format(optim_etf_tracking_error))

Returns
ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 -0.00011130  0.00113194  0.00007320 -0.00001672 -0.00008104   
2013-07-03  0.00009843  0.00027582  0.00000241 -0.00006029  0.00000816   
2013-07-05  0.00002715 -0.00040137  0.00005890  0.00006740  0.00012121   
2013-07-08  0.00003001 -0.00028371  0.00011407  0.00004834  0.00000600   
2013-07-09  0.00012530  0.00087887 -0.00004184 -0.00006519 -0.00003894   
2013-07-10 -0.00005531 -0.00019167  0.00006914  0.00000000 -0.00008238   
2013-07-11  0.00005887  0.00077888  0.00003121  0.00007636  0.00004733   
2013-07-12  0.00005528 -0.00009098  0.00014726 -0.00000487  0.00005961   
2013-07-15  0.00005756  0.00010896 -0.00004845  0.00001561 -0.00005004   
2013-07-16  0.00005407  0.00032207 -0.00009215  0.00002136 -0.00011804   
2013-07-17  0.00014078  0.0000

ticker             AAL       AAPL       ABBV         ABT         AGN  \
date                                                                   
2013-07-01         nan        nan        nan         nan         nan   
2013-07-02 -0.00011130 0.00113194 0.00007320 -0.00001672 -0.00008104   
2013-07-03 -0.00001287 0.00140777 0.00007560 -0.00007701 -0.00007289   
2013-07-05  0.00001428 0.00100640 0.00013450 -0.00000961  0.00004832   
2013-07-08  0.00004429 0.00072269 0.00024858  0.00003873  0.00005432   
2013-07-09  0.00016959 0.00160156 0.00020674 -0.00002646  0.00001538   
2013-07-10  0.00011428 0.00140989 0.00027588 -0.00002646 -0.00006700   
2013-07-11  0.00017315 0.00218877 0.00030709  0.00004991 -0.00001967   
2013-07-12  0.00022843 0.00209779 0.00045435  0.00004504  0.00003994   
2013-07-15  0.00028599 0.00220674 0.00040589  0.00006065 -0.00001010   
2013-07-16  0.00034006 0.00252881 0.00031374  0.00008201 -0.00012814   
2013-07-17  0.00048083 0.00254217 0.00033112  0.00009359 -0.0001

Optimized ETF Tracking Error: 0.05795012630412267


## Rebalance Portfolio Over Time
The single optimized ETF portfolio used the same weights for the entire history. This might not be the optimal weights for the entire period. Let's rebalance the portfolio over the same period instead of using the same weights. Implement `rebalance_portfolio` to rebalance a portfolio.

Reblance the portfolio every n number of days, which is given as `shift_size`. When rebalancing, you should look back a certain number of days of data in the past, denoted as `chunk_size`. Using this data, compute the optoimal weights using `get_optimal_weights` and `get_covariance_returns`.

In [26]:
def rebalance_portfolio(returns, index_weights, shift_size, chunk_size):
    """
    Get weights for each rebalancing of the portfolio.

    Parameters
    ----------
    returns : DataFrame
        Returns for each ticker and date
    index_weights : DataFrame
        Index weight for each ticker and date
    shift_size : int
        The number of days between each rebalance
    chunk_size : int
        The number of days to look in the past for rebalancing

    Returns
    -------
    all_rebalance_weights  : list of Ndarrays
        The ETF weights for each point they are rebalanced
    """
    assert returns.index.equals(index_weights.index)
    assert returns.columns.equals(index_weights.columns)
    assert shift_size > 0
    assert chunk_size >= 0
    
    print("Returns")
    print(returns)
    
    print("Chunk size")
    print(chunk_size)
    print("Length of returns data")
    print(len(returns))
    print("Shift size")
    print(shift_size)
    
    print("Index weights")
    print(index_weights)
    print("Iloc -1")
    print(index_weights.iloc[-1])
    
    all_rebalance_weights = []
    for i in range(chunk_size, len(returns), shift_size):
        covariance_returns = get_covariance_returns(returns[(i - chunk_size):i])
        print("Cov returns")
        print(covariance_returns)
        optimal_rebalanced_weights = get_optimal_weights(covariance_returns,
                                                         index_weights[(i - chunk_size):i].iloc[-1])
        print("Rebalanced weights")
        print(optimal_rebalanced_weights)
        all_rebalance_weights.append(optimal_rebalanced_weights)
    return all_rebalance_weights

project_tests.test_rebalance_portfolio(rebalance_portfolio)

Returns
                  RDXD        ZSEJ         YZE
2001-04-14         nan         nan         nan
2001-04-15 -0.02202381  0.02265285  0.01441961
2001-04-16  0.01947657  0.00551985  0.00047382
2001-04-17  0.00537313 -0.00803232  0.01160313
2001-04-18  0.00593824 -0.00567773  0.02247191
2001-04-19  0.02479339  0.01758824 -0.00824176
2001-04-20 -0.01094470 -0.00383568  0.01361958
2001-04-21  0.01164822  0.01558719  0.00614894
2001-04-22  0.01093840 -0.00182079  0.02900868
2001-04-23  0.01138952  0.00218049 -0.00954495
2001-04-24  0.01069820  0.00644535 -0.01815329
Chunk size
4
Length of returns data
11
Shift size
2
Index weights
                 RDXD       ZSEJ        YZE
2001-04-14 0.00449404 0.11586048 0.00359727
2001-04-15 0.00403487 0.12534048 0.00344280
2001-04-16 0.00423485 0.12854258 0.00347404
2001-04-17 0.00395679 0.12434660 0.00335064
2001-04-18 0.00368729 0.11750295 0.00333929
2001-04-19 0.00369562 0.11447422 0.00325973
2001-04-20 0.00379612 0.11088075 0.00317340
2001-04-21

Run the following cell to rebalance the portfolio using `rebalance_portfolio`.

In [27]:
chunk_size = 250
shift_size = 5
all_rebalance_weights = rebalance_portfolio(returns, index_weights, shift_size, chunk_size)

Returns
ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-01         nan         nan         nan         nan         nan   
2013-07-02 -0.02202381  0.02265285  0.01441961 -0.00485298 -0.01283482   
2013-07-03  0.01947657  0.00551985  0.00047382 -0.01749857  0.00129209   
2013-07-05  0.00537313 -0.00803232  0.01160313  0.01956204  0.01919510   
2013-07-08  0.00593824 -0.00567773  0.02247191  0.01403207  0.00094959   
2013-07-09  0.02479339  0.01758824 -0.00824176 -0.01892121 -0.00616650   
2013-07-10 -0.01094470 -0.00383568  0.01361958  0.00000000 -0.01304590   
2013-07-11  0.01164822  0.01558719  0.00614894  0.02216465  0.00749577   
2013-07-12  0.01093840 -0.00182079  0.02900868 -0.00141363  0.00944000   
2013-07-15  0.01138952  0.00218049 -0.00954495  0.00453001 -0.00792519   
2013-07-16  0.01069820  0.00644535 -0.01815329  0.00620068 -0.01869308   
2013-07-17  0.02785515  0.0002

Optimal Xs:
[0.01043134 0.06006002 0.01145332 0.00460319 0.00899074 0.00659741
 0.00588434 0.00543873 0.01913355 0.00440472 0.00117287 0.00498903
 0.00982399 0.02170975 0.00656725 0.00762632 0.01871608 0.00315683
 0.01490108 0.00299942 0.00180181 0.01017089 0.00302964 0.00757446
 0.00280221 0.00379319 0.00894089 0.00609675 0.01479801 0.00855455
 0.01117655 0.00342065 0.00574597 0.0052358  0.0066932  0.06960769
 0.00447415 0.00371878 0.00759784 0.01160758 0.01144284 0.00780362
 0.0217761  0.02548132 0.00738601 0.01097032 0.0083364  0.00317682
 0.0111048  0.01594194 0.01052272 0.01329633 0.00202779 0.01358219
 0.00451156 0.00311991 0.0050552  0.00628738 0.00545589 0.00816001
 0.01323018 0.00557249 0.01257088 0.00812513 0.00680572 0.01944452
 0.01416098 0.0194583  0.00839333 0.00246675 0.0137056  0.00461931
 0.00608005 0.01084456 0.01092437 0.01692651 0.0077317  0.0113174
 0.00577372 0.00556129 0.03248384 0.00983902 0.00390546 0.00569
 0.00331695 0.00602821 0.00490272 0.00619657 0.0030922

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-16  0.01069820  0.00644535 -0.01815329  0.00620068 -0.01869308   
2013-07-17  0.02785515  0.00026732  0.00342388  0.00336134 -0.00618691   
2013-07-18 -0.00162602  0.00336502  0.00818926 -0.00335008  0.01859436   
2013-07-19 -0.01031488 -0.01576809  0.00451264  0.00476190  0.00860474   
2013-07-22 -0.00438837  0.00320038  0.01010782 -0.00195149  0.02001276   
2013-07-23 -0.00550964 -0.01717060 -0.01467645  0.02458101 -0.01188150   
2013-07-24  0.02493075  0.05136161 -0.01512074 -0.00627045  0.00268966   
2013-07-25  0.01783784 -0.00456289  0.01374885  0.00356653  0.01656805   
2013-07-26  0.01380775  0.00567845  0.01243219  0.00546747  0.02995731   
2013-07-29  0.00733368  0.01541985  0.00602813 -0.00108755  0.01333735   
2013-07-30 -0.00156006  0.01234954 -0.00798935  0.00381056  0.00669244   
2013-07-31  0.00781250 -0.00174270  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2013-07-23 -0.00550964 -0.01717060 -0.01467645  0.02458101 -0.01188150   
2013-07-24  0.02493075  0.05136161 -0.01512074 -0.00627045  0.00268966   
2013-07-25  0.01783784 -0.00456289  0.01374885  0.00356653  0.01656805   
2013-07-26  0.01380775  0.00567845  0.01243219  0.00546747  0.02995731   
2013-07-29  0.00733368  0.01541985  0.00602813 -0.00108755  0.01333735   
2013-07-30 -0.00156006  0.01234954 -0.00798935  0.00381056  0.00669244   
2013-07-31  0.00781250 -0.00174270  0.01744966 -0.00677874 -0.00819914   
2013-08-01  0.00155039  0.00916182 -0.00505717  0.00573301  0.01124600   
2013-08-02 -0.02373581  0.01284061  0.00154696 -0.00244300  0.00081013   
2013-08-05  0.01321353  0.01493925 -0.01345984 -0.00816327  0.00706454   
2013-08-06 -0.01304121 -0.00894664  0.00380228 -0.00960219 -0.00898794   
2013-08-07 -0.00264271 -0.00058033 -0.

   2.60898348e-05  7.31542291e-05]]
Index weights
ticker
AAL     0.00849226
AAPL    0.07608856
ABBV    0.01047717
ABT     0.00303387
AGN     0.00557975
AIG     0.00716587
AMAT    0.01241428
AMGN    0.00650348
AMZN    0.11137187
APC     0.00453987
AVGO    0.00463675
AXP     0.00649319
BA      0.01303572
BAC     0.01010698
BIIB    0.00636377
BMY     0.00504845
C       0.00937273
CAT     0.00736031
CBS     0.01407632
CELG    0.00594237
CHTR    0.00160974
CMCSA   0.00973875
CMG     0.00772954
COP     0.00448885
COST    0.00311746
CRM     0.00519212
CSCO    0.01257292
CVS     0.00466246
CVX     0.00809391
DAL     0.00692370
           ...    
NVDA    0.00219131
ORCL    0.00549507
OXY     0.00405443
PEP     0.00459460
PFE     0.00729263
PG      0.00855017
PM      0.00371217
PXD     0.00375321
QCOM    0.01738429
REGN    0.00215466
SBUX    0.01349015
SLB     0.01135209
T       0.01050841
TGT     0.00267288
TWX     0.00876577
TXN     0.00771068
UAL     0.01058512
UNH     0.00514908
UNP     0.00

...

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-05-24  0.01323668  0.01524422  0.02360877  0.01632325  0.01498825   
2016-05-25  0.00062208  0.01756895  0.00856672  0.01843075 -0.00454367   
2016-05-26 -0.02051601  0.00793013  0.01110748  0.00542916  0.01979372   
2016-05-27  0.00444303 -0.00059755  0.01308562  0.01054256  0.01540713   
2016-05-31  0.00821485 -0.00488291  0.00350821  0.00839695 -0.00080529   
2016-06-01  0.00125353 -0.01401963 -0.00158907 -0.00328034  0.02820785   
2016-06-02 -0.00876369 -0.00751574  0.03597008  0.00075949  0.01947195   
2016-06-03 -0.02715504  0.00204666 -0.00138270 -0.00885403 -0.00064746   
2016-06-06  0.01460565  0.00725082 -0.03353846 -0.00025523  0.00101231   
2016-06-07  0.03518874  0.00405556  0.00445718 -0.00612714  0.00934428   
2016-06-08  0.00463535 -0.00090882 -0.02171157 -0.00051374  0.00172331   
2016-06-09  0.02737619  0.00717607 -0.

Optimal Xs:
[0.0058274  0.06688633 0.00526154 0.00762429 0.00751789 0.01099607
 0.00602839 0.00830102 0.06967199 0.00641697 0.00620214 0.0028512
 0.00639276 0.02314275 0.00421386 0.00523243 0.01334278 0.00602816
 0.00244678 0.00602349 0.00630696 0.01466168 0.00462729 0.00963581
 0.01585474 0.00968059 0.01000206 0.00543657 0.00763022 0.00577993
 0.01342609 0.00466142 0.00365768 0.00278656 0.00582896 0.04601155
 0.00228779 0.00293579 0.00442267 0.01625148 0.00504509 0.01067966
 0.02453062 0.03278176 0.0079265  0.00898746 0.01301683 0.00709386
 0.00720953 0.0079449  0.00998791 0.0136009  0.00393789 0.00995531
 0.00343091 0.00474168 0.00731744 0.00522144 0.00955114 0.00621773
 0.00800171 0.00810273 0.00222786 0.0046389  0.00453043 0.02744233
 0.01067466 0.0158369  0.0061811  0.05556694 0.00620026 0.00543056
 0.00711266 0.00730384 0.00738839 0.00513907 0.00380511 0.00922353
 0.0043653  0.00762639 0.01220375 0.01000725 0.0039476  0.00472822
 0.00449129 0.00415787 0.00556781 0.0085157  0.0037

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-15  0.00428195 -0.00328340  0.00834725 -0.00610728 -0.02031954   
2016-06-16 -0.04427681  0.00422071  0.00827815  0.00187016 -0.00773605   
2016-06-17  0.00686342 -0.02275756 -0.01461412 -0.00293333 -0.00943993   
2016-06-20  0.01261077 -0.00241267  0.00166639  0.00962824  0.00089343   
2016-06-21  0.01043420  0.00851735 -0.00216270 -0.00052980 -0.01576979   
2016-06-22 -0.00433045 -0.00375352  0.00683561  0.02676915 -0.01295616   
2016-06-23  0.01472064  0.00575615  0.01523431  0.02297367  0.02170203   
2016-06-24 -0.10814375 -0.02809573 -0.02365030 -0.04340146 -0.03336046   
2016-06-27 -0.06580407 -0.01456103 -0.01971266 -0.02532313 -0.03650540   
2016-06-28  0.05935892  0.01684050  0.02232447  0.01650880  0.04708479   
2016-06-29  0.03474038  0.00865477  0.03033839  0.02689031  0.01242754   
2016-06-30  0.02202166  0.01271186  0.

ticker             AAL        AAPL        ABBV         ABT         AGN  \
date                                                                     
2016-06-22 -0.00433045 -0.00375352  0.00683561  0.02676915 -0.01295616   
2016-06-23  0.01472064  0.00575615  0.01523431  0.02297367  0.02170203   
2016-06-24 -0.10814375 -0.02809573 -0.02365030 -0.04340146 -0.03336046   
2016-06-27 -0.06580407 -0.01456103 -0.01971266 -0.02532313 -0.03650540   
2016-06-28  0.05935892  0.01684050  0.02232447  0.01650880  0.04708479   
2016-06-29  0.03474038  0.00865477  0.03033839  0.02689031  0.01242754   
2016-06-30  0.02202166  0.01271186  0.00161786  0.01918590  0.00234223   
2016-07-01  0.03602967  0.00303347  0.01292198  0.00585093  0.01267904   
2016-07-05 -0.01363791 -0.00938575 -0.01259767 -0.00252908  0.00846082   
2016-07-06 -0.02004839  0.00568481  0.02341731  0.03524341  0.00415254   
2016-07-07  0.03703704  0.00429185  0.00094682  0.01298065  0.00434636   
2016-07-08  0.02176871  0.00771315  0.

Optimal Xs:
[0.00329252 0.06289451 0.0048217  0.00433544 0.00774756 0.00404509
 0.00796868 0.00874334 0.05738806 0.0034696  0.01296664 0.00346045
 0.0102701  0.02351968 0.00610458 0.00525516 0.0160002  0.00496492
 0.0034945  0.00886234 0.00534227 0.01195217 0.00705613 0.00668115
 0.01748012 0.00731099 0.01169978 0.01151092 0.00615846 0.00539261
 0.01039776 0.00409504 0.00377144 0.0030607  0.00560233 0.04726814
 0.00280764 0.00453575 0.00442433 0.01296807 0.01668187 0.00670815
 0.02595196 0.0251588  0.00960858 0.00385883 0.01042526 0.00281832
 0.0054681  0.01067626 0.01259576 0.01460337 0.00348971 0.00580133
 0.00413074 0.00412972 0.00668429 0.00497484 0.00604786 0.0039408
 0.00515885 0.00496248 0.00315253 0.00824661 0.00425302 0.02312832
 0.01925679 0.01615561 0.00714692 0.06881215 0.02514436 0.00360734
 0.00523856 0.00792227 0.00645078 0.00348685 0.00309917 0.00681107
 0.01031405 0.00565288 0.00876858 0.0113524  0.00490421 0.00372342
 0.00640379 0.00334277 0.00724515 0.00541137 0.0040

## Portfolio Turnover
With the portfolio rebalanced, we need to use a metric to measure the cost of rebalancing the portfolio. Implement `get_portfolio_turnover` to calculate the annual portfolio turnover. We'll be using the formulas used in the classroom:

$ AnnualizedTurnover =\frac{SumTotalTurnover}{NumberOfRebalanceEvents} * NumberofRebalanceEventsPerYear $

$ SumTotalTurnover =\sum_{t,n}{\left | x_{t,n} - x_{t+1,n} \right |} $ Where $ x_{t,n} $ are the weights at time $ t $ for equity $ n $.

$ SumTotalTurnover $ is just a different way of writing $ \sum \left | x_{t_1,n} - x_{t_2,n} \right | $

In [48]:
def get_portfolio_turnover(all_rebalance_weights, shift_size, rebalance_count, n_trading_days_in_year=252):
    """
    Calculage portfolio turnover.

    Parameters
    ----------
    all_rebalance_weights : list of Ndarrays
        The ETF weights for each point they are rebalanced
    shift_size : int
        The number of days between each rebalance
    rebalance_count : int
        Number of times the portfolio was rebalanced
    n_trading_days_in_year: int
        Number of trading days in a year

    Returns
    -------
    portfolio_turnover  : float
        The portfolio turnover
    """
    assert shift_size > 0
    assert rebalance_count > 0
    
    print("All rebalance weights")
    print(all_rebalance_weights)
    
    print("Rebalance count")
    print(rebalance_count)

    sumTotalTurnover = 0
    for i in range(0,rebalance_count):
        diff = np.absolute(all_rebalance_weights[i] - all_rebalance_weights[i+1])
        print(diff)
        sumTotalTurnover += diff
        
    sumTotalTurnover = sumTotalTurnover.sum()
    print("Sum Total Turnover")
    print(sumTotalTurnover)
    
    nr_rebalance_events_per_year = n_trading_days_in_year / shift_size 
    print("Nr of rebalance events per year")
    print(nr_rebalance_events_per_year)
    
    portfolio_turnover = (sumTotalTurnover / rebalance_count) * nr_rebalance_events_per_year
    
    return portfolio_turnover

project_tests.test_get_portfolio_turnover(get_portfolio_turnover)

All rebalance weights
[array([1.22050335e-04, 3.01991574e-04, 9.99575958e-01]), array([1.30570982e-05, 8.11299880e-06, 9.99978830e-01]), array([0.39174818, 0.56076878, 0.04748304])]
Rebalance count
2
[0.00010899 0.00029388 0.00040287]
[0.39173512 0.56076067 0.95249579]
Sum Total Turnover
1.905797323172624
Nr of rebalance events per year
84.0
Tests Passed


Run the following cell to get the portfolio turnover from  `get_portfolio turnover`.

In [49]:
print(get_portfolio_turnover(all_rebalance_weights, shift_size, len(all_rebalance_weights) - 1))

All rebalance weights
[array([0.01043134, 0.06006002, 0.01145332, 0.00460319, 0.00899074,
       0.00659741, 0.00588434, 0.00543873, 0.01913355, 0.00440472,
       0.00117287, 0.00498903, 0.00982399, 0.02170975, 0.00656725,
       0.00762632, 0.01871608, 0.00315683, 0.01490108, 0.00299942,
       0.00180181, 0.01017089, 0.00302964, 0.00757446, 0.00280221,
       0.00379319, 0.00894089, 0.00609675, 0.01479801, 0.00855455,
       0.01117655, 0.00342065, 0.00574597, 0.0052358 , 0.0066932 ,
       0.06960769, 0.00447415, 0.00371878, 0.00759784, 0.01160758,
       0.01144284, 0.00780362, 0.0217761 , 0.02548132, 0.00738601,
       0.01097032, 0.0083364 , 0.00317682, 0.0111048 , 0.01594194,
       0.01052272, 0.01329633, 0.00202779, 0.01358219, 0.00451156,
       0.00311991, 0.0050552 , 0.00628738, 0.00545589, 0.00816001,
       0.01323018, 0.00557249, 0.01257088, 0.00812513, 0.00680572,
       0.01944452, 0.01416098, 0.0194583 , 0.00839333, 0.00246675,
       0.0137056 , 0.00461931, 0.006080

[4.07089977e-03 3.77927801e-02 2.87432245e-03 1.32702387e-03
 6.65208060e-02 1.02039204e-03 1.67879866e-05 2.02316081e-03
 1.17022963e-02 8.53314885e-03 5.35385147e-04 8.72647338e-04
 2.26796417e-03 4.40073876e-03 3.97819956e-05 5.51362363e-04
 1.65426699e-03 1.71281079e-03 2.01683198e-03 1.11766435e-03
 8.30854729e-03 5.12199414e-02 9.65336531e-04 3.09112905e-03
 1.86395851e-03 6.15629515e-04 4.03199345e-04 5.72349867e-04
 1.47701453e-03 2.83748228e-03 6.88667395e-03 9.02077963e-04
 3.55851422e-03 6.14179514e-04 2.75500317e-03 7.69860231e-03
 8.57124973e-04 9.35008370e-04 3.81503110e-03 3.22472376e-03
 1.18865279e-02 7.17523310e-04 4.91600257e-03 2.72969729e-03
 2.12867074e-04 5.79541285e-02 7.77619994e-03 3.32008493e-04
 1.10288720e-03 7.80268606e-03 5.01272035e-03 2.69710958e-03
 4.67083076e-03 8.21225380e-04 1.59093931e-03 6.71114395e-04
 1.34558585e-03 2.23403584e-03 2.77555498e-03 2.41397215e-03
 1.05148671e-03 2.08980510e-03 4.86957765e-03 6.44819624e-03
 2.27970042e-03 6.324195

That's it! You've built a smart beta portfolio in part 1 and did portfolio optimization in part 2. You can now submit your project.

## Submission
Now that you're done with the project, it's time to submit it. Click the submit button in the bottom right. One of our reviewers will give you feedback on your project with a pass or not passed grade. You can continue to the next section while you wait for feedback.